In [1]:
import xarray as xr
import pandas as pd
import matplotlib.pyplot as plt
from oggm.utils import file_downloader, mkdir
import os

In [2]:
df_rgi = pd.read_hdf(file_downloader('https://cluster.klima.uni-bremen.de/~oggm/rgi/rgi62_stats.h5'))
df_rgi = df_rgi.loc[df_rgi.Connect != 2]

In [3]:
periods = ['1851-1870', '1901-1920', '1951-1970', '1995-2014']

In [4]:
val_per_reg = dict()

for reg in range(1, 20):
    reg = f'RGI{reg:02d}'
    df = pd.DataFrame()
    for period in periods:
        try:
            with xr.open_dataset(f'output/{reg}/gfdl-esm4_historical_{period}.nc') as ds:
                df[period] = ~ ds.volume.isel(time=0).isnull().to_series()
        except:
            continue
    if len(df) > 0:
        val_per_reg[reg] = df

In [5]:
valid_ids_per_reg = dict()
area_stats = pd.DataFrame()
for reg in range(1, 20):
    reg = f'RGI{reg:02d}'
    if reg not in val_per_reg:
        continue
    df = val_per_reg[reg]
    val_ids = df.loc[df.all(axis=1)].index
    valid_ids_per_reg[reg] = val_ids
    
    # Stats
    df_rgi_reg = df_rgi.loc[df_rgi['O1Region'] == reg[-2:]]
    area_stats.loc[reg, 'all'] = 1 - df_rgi_reg.loc[val_ids].Area.sum() / df_rgi_reg.Area.sum()
    
    # Stats per period
    for period in periods:
        val_ids = df.loc[df[period]].index
        area_stats.loc[reg, period] = 1 - df_rgi_reg.loc[val_ids].Area.sum() / df_rgi_reg.Area.sum()

In [6]:
area_stats

all  1851-1870  1901-1920  1951-1970  1995-2014
RGI01  0.074457   0.062293   0.072668   0.061221   0.046917
RGI02  0.004066   0.003332   0.002775   0.003397   0.001724
RGI03  0.233266   0.231532   0.160427   0.142802   0.051544
RGI04  0.004446   0.004441   0.002969   0.003477   0.001914
RGI05  0.144903   0.056151   0.036413   0.101204   0.009923
RGI06  0.000654   0.000654   0.000518   0.000365   0.000133
RGI07  0.241089   0.185221   0.178951   0.241075   0.182812
RGI08  0.007665   0.004551   0.006647   0.006885   0.001863
RGI09  0.244081   0.237817   0.206094   0.202229   0.208970
RGI10  0.057564   0.055661   0.050930   0.050437   0.044980
RGI11  0.000395   0.000338   0.000323   0.000378   0.000290
RGI12  0.120687   0.120687   0.120262   0.120457   0.119908
RGI13  0.057657   0.042758   0.044504   0.047213   0.011817
RGI15  0.010641   0.006454   0.010008   0.006664   0.001936
RGI16  0.051022   0.051022   0.030218   0.023171   0.000225
RGI18  0.001835   0.001835   0.001085   0.001679   0.000307
RGI19  0.461404   0.439012   0.146583   0.400579   0.163982

In [13]:
reset = False
for reg in range(1, 20):
    reg = f'RGI{reg:02d}'
    df = pd.DataFrame()
    for period in periods:
        odir = f'clean/{reg}/'
        of = f'{odir}/gfdl-esm4_historical_{period}.nc'
        if not reset and os.path.exists(of):    
            continue
        try:
            with xr.open_dataset(f'output/{reg}/gfdl-esm4_historical_{period}.nc') as ds:
                print(reg, 'found')
                val_ids = valid_ids_per_reg[reg]
                ds = ds[['volume', 'area']].load().sel(rgi_id=val_ids)
                mkdir(odir)
                ds.to_netcdf(f'{odir}/gfdl-esm4_historical_{period}.nc')
        except FileNotFoundError:
            print(reg, 'not found')
            continue

RGI13 found
RGI13 found
RGI13 found
RGI13 found
RGI14 not found
RGI14 not found
RGI14 not found
RGI14 not found
RGI17 not found
RGI17 not found
RGI17 not found
RGI17 not found
